# Random Forest

In [1]:
from random import seed
from random import randrange
from csv import reader
from math import sqrt
import json


In [2]:
 # Load a CSV file. Definition of the function to read the csv and create dataset here
def load_csv(filename):
	dataset = list()
	with open(filename, 'r') as file:
		csv_reader = reader(file)
		for row in csv_reader:
			if not row:
				continue
			dataset.append(row)
	return dataset


In [3]:
# Convert string column to float
def str_column_to_float(dataset, column):
	for row in dataset:
		row[column] = float(row[column].strip())
 
# Convert string column to integer
def str_column_to_int(dataset, column):
	class_values = [row[column] for row in dataset] # extract the values of the column (here the classes of the dataset, mine and rocks)
	unique = set(class_values) # calculate how many unique class values there are and store them into a set: a list with unique values
	lookup = dict() #create a dictionnary
	for i, value in enumerate(unique): # loops through the set / enumerate gives you a tuple with an index number and a value /common way to get indexes from a list
		lookup[value] = i # the key of the dictonnary is the value: mine or rock; and the value is a number: 0 or 1
	for row in dataset: # loops through the rows of the dataset
		row[column] = lookup[row[column]] #replaces the value of the column: rock or mine, with the index value: 0 or 1;
	return lookup # the code returns the lookup table


In [4]:
# Split a dataset into k folds
def cross_validation_split(dataset, n_folds):
	dataset_split = list() #create a list 
	dataset_copy = list(dataset) # creates a list of the dataset. You could use the copy library
	fold_size = int(len(dataset) / n_folds) # the size of the fold is equal to the length of the dataset divided by the amount of folds
	print("fold size:")
	print(fold_size) 
	for i in range(n_folds): #loops the amount of folds : generate another list with numbers from 0 up to n_fold
		fold = list() #create a list
		while len(fold) < fold_size: # as long as the length of the list is inferior to the defined fold size
			index = randrange(len(dataset_copy)) # return a random integer between 0 and the total length of the dataset and store it in index
			fold.append(dataset_copy.pop(index)) # append an observation at the index and removes it from the dataset
		dataset_split.append(fold) # append the fold to the list dataset_split
		#print("______________")
		#print("dataset split:")
		#print(dataset_split)
		#print("______________")
	return dataset_split #return the dataset_split, a list of folds


In [5]:
# Calculate accuracy percentage
def accuracy_metric(actual, predicted):
	correct = 0 #create a correct variable
	for i in range(len(actual)): # loops up to the length of the actual list
		if actual[i] == predicted[i]: # compares the actual vs the predicted
			correct += 1 #if correct add one to the correct variable. Count the number of correct guesses
	return correct / float(len(actual)) * 100.0 #gives a percentage by dividing the correct guesses by the length of the actual classes and multiply by a hundred
 

In [6]:
# Evaluate an algorithm using a cross validation split
def evaluate_algorithm(dataset, algorithm, n_folds, *args):
	folds = cross_validation_split(dataset, n_folds) #return the list of folds
	scores = list() #creates a list called scores
	for fold in folds: #loops through the folds
		train_set = list(folds) #creates a copy of the list of folds 
		train_set.remove(fold) #remove one fold: for testing?
		train_set = sum(train_set, []) # concatenate all folds, a list of lists, into one list. can be done with itertools.chain
		test_set = list() # create another list
		for row in fold: # iterates through fold
			row_copy = list(row) # creates a copy of the list
			test_set.append(row_copy) # append the list to the test_set
			row_copy[-1] = None # set the classification to none. Changes the last column to none.
		predicted = algorithm(train_set, test_set, *args) # what is doing the prediction takes for argument the train and test set and returns prediction for the test set
		actual = [row[-1] for row in fold] # list comprehension: list of actual classes from fold.
		accuracy = accuracy_metric(actual, predicted) # function that compares the actual vs the predicted to give an idea of the accuracy of the prediction
		scores.append(accuracy) #append the accuracy to the list of scores
	return scores
 

In [7]:


# Split a dataset based on an attribute/feature and an attribute/feature value
def test_split(index, value, dataset):
	left, right = list(), list() # create two lists for each side
	for row in dataset: #iterate through each row of the dataset
		if row[index] < value: #if the feature value of the current row is below the feature value given
			left.append(row) # append it to the left list
		else:
			right.append(row) # append it to the right list
	return left, right # return the two lists
 
# Calculate the Gini index for a split dataset
def gini_index(groups, classes):
	# count all samples at split point
	n_instances = float(sum([len(group) for group in groups])) #counting the total number of instances into float for divisions
	# sum weighted Gini index for each group
	gini = 0.0 #gini variable
	for group in groups: #for each of the group
		size = float(len(group)) #number of instances in each group
		# avoid divide by zero
		if size == 0:
			continue
		score = 0.0
		# score the group based on the score for each class
		for class_val in classes:
			p = [row[-1] for row in group].count(class_val) / size #count the number of instances for the current class in the group and divide it by the total size of the group
			score += p * p #amplifying the difference (exponential ?)
		# weight the group score by its relative size
		gini += (1.0 - score) * (size / n_instances) # substract the score from 1 and multiply it by the relative size of the group compared to the dataset
	return gini
 
# Select the best split point for a dataset
def get_split(dataset, n_features):
	class_values = list(set(row[-1] for row in dataset)) # creates a list of the set for the class values. Here encoded as 1 and 0 . We already did it before
	b_index, b_value, b_score, b_groups = 999, 999, 999, None # assign values to variables
	features = list() #creates a list. 
	while len(features) < n_features: # as long as features is smaller that the actual number of desirable features= n_features
		index = randrange(len(dataset[0])-1) # create a random number between 0 and the number of columns-1= minus the class
		if index not in features: # if the column names is not already in the features
			features.append(index) # append the column name
	for index in features: # for each column name(=index name) in features
		for row in dataset: # for each row of the dataset
			groups = test_split(index, row[index], dataset) # get two lists. very computationnaly heavy. Why not do the ordering first?
			gini = gini_index(groups, class_values) # get the gini value
			if gini < b_score: #if the gini value is smaller than b_score (b for best?). this should always be true for the first operation. Test against the best option
				b_index, b_value, b_score, b_groups = index, row[index], gini, groups # update the values for the best option
	return {'index':b_index, 'value':b_value, 'groups':b_groups} #return the best option in the form of a dictionnary
 
# Create a terminal node value
# Returns the most popular value in the group
def to_terminal(group):
	outcomes = [row[-1] for row in group] #takes the class of the group elements and put it in a list
	return max(set(outcomes), key=outcomes.count) #return the class that appears the most. set is counting the different class and the key is counting the number of occurences of this class. SPOOKY AND DENSE
 
# Create child splits for a node or make a terminal (node)
def split(node, max_depth, min_size, n_features, depth):
	left, right = node['groups'] #get the groups using the dictionnary node with the key groups
	del(node['groups']) #delete dictionnary element with key groups
	# check for a no split
	if not left or not right: #if one of the group is empty
		node['left'] = node['right'] = to_terminal(left + right) #call this function
		return 
	# check for max depth
	if depth >= max_depth: # checking if level is bigger or equal than maximum level of nodes
		node['left'], node['right'] = to_terminal(left), to_terminal(right) #if yes, so both nodes are terminal nodes
		return
	# process left child
	if len(left) <= min_size: # if the group is smaller or equal than the minimum size for a group
		node['left'] = to_terminal(left) #left node is a terminal node
	else:
		node['left'] = get_split(left, n_features) #create another split, another node from which to separate in two groups with a subset of a dataset
		split(node['left'], max_depth, min_size, n_features, depth+1) #recursion -> calls itself
	# process right child
	if len(right) <= min_size:
		node['right'] = to_terminal(right)
	else:
		node['right'] = get_split(right, n_features)
		split(node['right'], max_depth, min_size, n_features, depth+1)
 
# Build a decision tree
def build_tree(train, max_depth, min_size, n_features):
	root = get_split(train, n_features) #get the index, value and group (?) for the split. It's a dictionnary
	split(root, max_depth, min_size, n_features, 1) #depth is one
    # root is Node
    # Node: { index: int, value: float, left: Node|TerminalNode, right: Node|TerminalNode }
    # TerminalNode: { index: int, value: float, left: int(class), right: int(class) }
	return root #dictionnary with index, value, left, right
 
# Make a prediction with a decision tree
def predict(node, row):
	if row[node['index']] < node['value']: #if the feature value of the row is smaller of the feature value of the node
		if isinstance(node['left'], dict): # is it a node or a terminal node(children are not node)
			return predict(node['left'], row) #recursion if a node. the function calls itselft on the following left node
		else:
			return node['left'] # result if a terminal node
	else:
		if isinstance(node['right'], dict): # is it a node or a terminal node(children are not node)
			return predict(node['right'], row)#recursion if a node. the function calls itselft on the following right node
		else:
			return node['right']# result if a terminal node
 
# Create a random subsample from the dataset with replacement
def subsample(dataset, ratio):
	sample = list() #creates a list
	n_sample = round(len(dataset) * ratio) # rounds the multiplication of the length of the dataset with the sample.size: here 1. 
	while len(sample) < n_sample: # loop up until the length of the sample is the length of n_sample
		index = randrange(len(dataset)) #take a random number from 0 up to length of the dataset
		sample.append(dataset[index]) # append a sample whith this index
	return sample # return the list of sub-samples
 
# Make a prediction with a list of bagged trees
def bagging_predict(trees, row): 
	predictions = [predict(tree, row) for tree in trees] # we run the prediction in each tree, this gives a list of predictions of classes/votes. THE TREES ARE VOTING.
	return max(set(predictions), key=predictions.count) # we count the class with the maximum votes and return it as prediction
 
# Random Forest Algorithm
def random_forest(train, test, max_depth, min_size, sample_size, n_trees, n_features):
	trees = list() #create a list of trees
	for i in range(n_trees): 
		sample = subsample(train, sample_size) # create subsamples 
		tree = build_tree(sample, max_depth, min_size, n_features) #build the tree
		trees.append(tree)#append the list       
	with open("model.json", "w") as out_file:  
		json.dump(trees, out_file, indent = 6)
	predictions = [bagging_predict(trees, row) for row in test] # testing with test data, running the prediction on every row. THE FOREST VOTES ON EVERY ROW
	return(predictions) # we return the predicted class of each of the rows as a list. THE PREDICTIONS OF THE FOREST
 

In [8]:
from random import random

In [9]:
# Test the random forest algorithm
seed(2) #put the random generator in a certain state -> makes it deterministic otherwise python takes the time of the computer
#print(random())
#print(random())
#seed(2)
#print(random())



In [10]:
# load and prepare data
filename = 'iris.csv'
#filename = 'iris.csv'

dataset = load_csv(filename)
#print(dataset)


In [11]:
# convert string attributes to integers
for i in range(0, len(dataset[0])-1):
	str_column_to_float(dataset, i)
# convert class column to integers
#str_column_to_int(dataset, len(dataset[0])-1) #this function loops through the rows and transforms the words mine and roch into 1 and 0
#print(dataset)

In [12]:
# evaluate algorithm
n_folds = 5 #the data is randomly sampled into 5 subsamples, one is kept for testing the 4 else are used for training.
max_depth = 10 #
min_size = 1
sample_size = 1.0 #fixed, can be changed to reduces the amount of subsampling, if it is smaller than one.


In [13]:
n_features = int(sqrt(len(dataset[0])-1)) #it specifies the size of the feature subset for the folds, where the size is close to the square root of the total number of features
for n_trees in [1, 5, 10]: # will loop three times by taking n_trees equals one, n_trees equals five and n_trees equals ten successively.
	scores = evaluate_algorithm(dataset, random_forest, n_folds, max_depth, min_size, sample_size, n_trees, n_features)
	print('Trees: %d' % n_trees)
	print('Scores: %s' % scores)
	print('Mean Accuracy: %.3f%%' % (sum(scores)/float(len(scores))))

fold size:
30
Trees: 1
Scores: [100.0, 93.33333333333333, 90.0, 100.0, 93.33333333333333]
Mean Accuracy: 95.333%
fold size:
30
Trees: 5
Scores: [96.66666666666667, 96.66666666666667, 100.0, 93.33333333333333, 93.33333333333333]
Mean Accuracy: 96.000%
fold size:
30
Trees: 10
Scores: [90.0, 96.66666666666667, 96.66666666666667, 86.66666666666667, 100.0]
Mean Accuracy: 94.000%


In [19]:
with open ("model.json", "r") as in_file:
	trees=json.load(in_file)
	prediction=bagging_predict(trees,dataset[55])
	print(prediction)

Iris Versicolor
